In [1]:
import pandas as pd
from pandas import DataFrame
import numpy as np
from collections import Counter

In [2]:
person_names = ['demographics','family_hist_list', 'encounters','systemic_disease_list', 'SNOMED_problem_list']

In [3]:
path = ''
dfs = [pd.read_pickle(path + name + '.pickle') for name in person_names]

In [4]:
dfs[0].head()

﻿Person_ID  Person_Nbr        DOB Gender  \
14132  18405351-AC64-46A2-A003-8F7889351A13          33 1948-10-15      F   
8747   4ACD51E8-4A9B-4AA6-B635-166ADA5EF02E          89 1955-09-04      M   
2129   DF25CE0F-E45A-44D2-BE43-F49FE4F5E280         112 1932-11-19      F   
6591   7027DD58-6465-496C-880A-A6E825C155A8         146 1948-12-19      F   
16909  395DD5E7-45F9-456E-A127-9AB929E872F7         196 1955-02-21      F   

                                        Race            Ethnicity        Zip  \
14132  Black/African American (Not Hispanic)  Declined to specify      60616   
8747                     Declined to specify  Declined to specify      60652   
2129                                     NaN                  NaN  606372549   
6591                     Declined to specify  Declined to specify      60615   
16909                    Declined to specify  Declined to specify      60615   

      Age_Censored  
14132         None  
8747          None  
2129          None  
6591          None  
16909         None

In [5]:
dfs[1].head()

Person_ID  Person_Nbr  \
47872  80d3df88-dddf-5ad3-7cc1-b7b1ac6151fa          33   
47869  80d3df88-dddf-5ad3-7cc1-b7b1ac6151fa          33   
47867  80d3df88-dddf-5ad3-7cc1-b7b1ac6151fa          33   
47871  80d3df88-dddf-5ad3-7cc1-b7b1ac6151fa          33   
47868  80d3df88-dddf-5ad3-7cc1-b7b1ac6151fa          33   

                 Date_Created       Code Code_System  \
47872 2014-12-18 14:47:15.980  160347007      SNOMED   
47869 2014-12-18 14:47:26.897  160274005      SNOMED   
47867 2014-12-18 14:47:28.590  160274005      SNOMED   
47871 2014-12-18 14:47:29.563  160267000      SNOMED   
47868 2014-12-18 15:55:35.837  439724007      SNOMED   

                        Family_History Relation  
47872                         Glaucoma   Father  
47869  No history of Diabetes mellitus   Mother  
47867  No history of Diabetes mellitus   Father  
47871           No history of Glaucoma   Mother  
47868                    Heart disease  Brother

In [46]:
list(dfs[1][dfs[1].Relation.notnull()].Relation.drop_duplicates())

['Father',
 'Mother',
 'Brother',
 'Sister',
 'Paternal uncle',
 'Maternal grandfather',
 'Maternal grandmother',
 'Daughter',
 'Maternal aunt',
 'Family',
 'Paternal grandmother',
 'Maternal uncle',
 'Paternal grandfather',
 'Son',
 'Cousin',
 'mother',
 'Younger brother',
 'Niece',
 'Twin brother',
 'Sister Daughter',
 "Mother's side",
 "Father's side",
 'siblings',
 'Sister (4 of them)',
 'Father and sister',
 'family history',
 'Aunt',
 'Cousins',
 'Maternal great aunt',
 'Unknown',
 'Nephew',
 'Multiple Relatives',
 'Parents',
 'Paternal aunt',
 'Family history',
 'Mother Father Sist',
 'Mother sister',
 'Uncle',
 'MGF',
 'MGM brother',
 'Brother sister',
 'Aunt (maternal)',
 'Sickle',
 'Mothers Side',
 'Fathers Side',
 'parents',
 'everyone',
 'Multiple',
 'father',
 'Mother & Father',
 'Motherfathersis',
 'Mother Sister',
 'Siblings',
 'Mother brother fat',
 'Brother mother',
 'Mother MGM',
 'Grandparents both',
 'father sisters',
 'Close relative',
 '(-) FHx of GLC',
 '10/11 si

In [6]:
dfs[2].head()

﻿Person_ID  Person_Nbr  \
10335  18405351-AC64-46A2-A003-8F7889351A13          33   
59383  4ACD51E8-4A9B-4AA6-B635-166ADA5EF02E          89   
56011  4ACD51E8-4A9B-4AA6-B635-166ADA5EF02E          89   
78800  4ACD51E8-4A9B-4AA6-B635-166ADA5EF02E          89   
3870   4ACD51E8-4A9B-4AA6-B635-166ADA5EF02E          89   

                                     Enc_ID   Enc_Nbr       Enc_Timestamp  
10335  97825c51-4462-eade-1c1d-2baa3400c033    123227 2014-12-18 14:00:00  
59383  a6d9d991-4ff4-79b5-304d-f1b2bff9d6d0  12870648 2012-10-16 03:45:00  
56011  fe5eb87c-39b3-4314-0172-4642d51de417   4126172 2014-03-12 15:30:00  
78800  ea3c2622-6d1d-53ab-ddf0-9764927f1507   9217142 2014-04-17 18:45:00  
3870   71d10fa4-3b0d-fa52-cfbd-ffd0f3d3532d  14968450 2014-05-25 10:45:00

 ### Process family history

In [7]:
# Create Date variable
from datetime import datetime
dfs[1]['Date'] = [datetime.strftime(item, '%Y-%m-%d') for item in dfs[1]['Date_Created']]

In [8]:
# Individual family history grouped by the relationship
# Date of collecting could be omited
family_hist_list = {k:{k1:[{'Code': a, 'Family_history': b}#, 'Date': c} 
                  for a,b#,c 
                           in zip(v1.Code, v1.Family_History)]#, v1.Date)]
              for k1, v1 in v.groupby('Relation')}
           for k,v in dfs[1].groupby('Person_Nbr')}

In [9]:
family_hist_list

{109227: {'Brother': [{'Code': '430679000',
    'Family_history': 'Diabetes mellitus type 2'}],
  'Father': [{'Code': '160274005',
    'Family_history': 'No history of Diabetes mellitus'},
   {'Code': '160267000', 'Family_history': 'No history of Glaucoma'}],
  'Mother': [{'Code': '416855002', 'Family_history': 'Diabetes mellitus'},
   {'Code': '160267000', 'Family_history': 'No history of Glaucoma'},
   {'Code': '160357008', 'Family_history': 'Hypertension'}]},
 622597: {'Father': [{'Code': '416855002',
    'Family_history': 'Diabetes mellitus'},
   {'Code': '160267000', 'Family_history': 'No history of Glaucoma'}],
  'Maternal grandmother': [{'Code': '160347007',
    'Family_history': 'Glaucoma'}],
  'Mother': [{'Code': '160274005',
    'Family_history': 'No history of Diabetes mellitus'},
   {'Code': '160267000', 'Family_history': 'No history of Glaucoma'}]},
 196620: {'Father': [{'Code': '416855002',
    'Family_history': 'Diabetes mellitus'},
   {'Code': 'NULL', 'Family_history': 

### Process demographics

In [10]:
len(dfs[0].Person_Nbr.drop_duplicates()) == len(dfs[0])
# There is no person duplicated in demographics

True

In [11]:
# Create age variable
dfs[0]['Age'] =[datetime.now().year - int(datetime.strftime(item, '%Y')) for item in dfs[0]['DOB']]

# Normalize zip code with only 5 digits
zip_code=[]
for item in dfs[0].Zip:
    zip_code.append(item[:5])
dfs[0]['zip_code'] = zip_code

In [12]:
# There is only one null case for zip code
dfs[0][dfs[0].zip_code=='NULL']

﻿Person_ID  Person_Nbr        DOB Gender  \
2065  4CCDD77B-12DF-4943-BA78-F387C3AD2182      542734 1927-05-07      M   

                                       Race               Ethnicity   Zip  \
2065  Black/African American (Not Hispanic)  Not Hispanic or Latino  NULL   

     Age_Censored  Age zip_code  
2065         None   90     NULL

In [13]:
dfs[0][dfs[0].Zip=='NULL']

﻿Person_ID  Person_Nbr        DOB Gender  \
2065  4CCDD77B-12DF-4943-BA78-F387C3AD2182      542734 1927-05-07      M   

                                       Race               Ethnicity   Zip  \
2065  Black/African American (Not Hispanic)  Not Hispanic or Latino  NULL   

     Age_Censored  Age zip_code  
2065         None   90     NULL

In [14]:
demographics=dfs[0].set_index('Person_Nbr')[['Age', 'Gender', 'Race', 'Ethnicity', 'zip_code', 'Age_Censored']].T.to_dict()

In [15]:
demographics

{109227: {'Age': 61,
  'Age_Censored': 'None',
  'Ethnicity': 'Not Hispanic or Latino',
  'Gender': 'F',
  'Race': 'Black/African American (Not Hispanic)',
  'zip_code': '60419'},
 622597: {'Age': 55,
  'Age_Censored': 'None',
  'Ethnicity': 'Declined to specify',
  'Gender': 'F',
  'Race': 'Declined to specify',
  'zip_code': '60426'},
 196620: {'Age': 52,
  'Age_Censored': 'None',
  'Ethnicity': 'Not Hispanic or Latino',
  'Gender': 'M',
  'Race': 'Black or African American',
  'zip_code': '60609'},
 884751: {'Age': 60,
  'Age_Censored': 'None',
  'Ethnicity': 'Unknown Ethnicity',
  'Gender': 'M',
  'Race': 'White',
  'zip_code': '60608'},
 819216: {'Age': 24,
  'Age_Censored': 'None',
  'Ethnicity': 'Hispanic or Latino',
  'Gender': 'F',
  'Race': 'Hispanic',
  'zip_code': '60647'},
 98322: {'Age': 60,
  'Age_Censored': 'None',
  'Ethnicity': 'Hispanic or Latino',
  'Gender': 'M',
  'Race': 'Hispanic',
  'zip_code': '60608'},
 1015827: {'Age': 64,
  'Age_Censored': 'None',
  'Ethnic

In [16]:
set(demographics.keys())&set(family_hist_list.keys())==set(family_hist_list)
# People in demographics have fully covered people in family_hist_list

True

### Process encounter list

In [17]:
# Create Date variable
dfs[2]['Enc_Date'] = [datetime.strftime(item, '%Y-%m-%d') for item in dfs[2]['Enc_Timestamp']]

In [19]:
Enc_list = {k:[{'Enc_Nbr': a, 'Enc_Date': b} for a,b in zip(v.Enc_Nbr, v.Enc_Date)] for k,v in dfs[2].groupby('Person_Nbr')}

In [20]:
Enc_list

{109227: [{'Enc_Date': '2016-07-29', 'Enc_Nbr': 4086734}],
 622597: [{'Enc_Date': '2013-05-02', 'Enc_Nbr': 16488561},
  {'Enc_Date': '2013-05-02', 'Enc_Nbr': 13216606},
  {'Enc_Date': '2014-12-19', 'Enc_Nbr': 6333408},
  {'Enc_Date': '2014-12-19', 'Enc_Nbr': 9923528}],
 196620: [{'Enc_Date': '2014-01-15', 'Enc_Nbr': 13975914}],
 884751: [{'Enc_Date': '2011-11-28', 'Enc_Nbr': 146465}],
 819216: [{'Enc_Date': '2013-07-12', 'Enc_Nbr': 5794803}],
 98322: [{'Enc_Date': '2012-12-06', 'Enc_Nbr': 10967288},
  {'Enc_Date': '2012-12-07', 'Enc_Nbr': 11328070},
  {'Enc_Date': '2013-01-07', 'Enc_Nbr': 11311562},
  {'Enc_Date': '2013-09-19', 'Enc_Nbr': 13085096},
  {'Enc_Date': '2014-08-09', 'Enc_Nbr': 11247025},
  {'Enc_Date': '2016-06-16', 'Enc_Nbr': 3689952},
  {'Enc_Date': '2016-06-16', 'Enc_Nbr': 9254247}],
 1015827: [{'Enc_Date': '2015-04-30', 'Enc_Nbr': 6960324},
  {'Enc_Date': '2016-07-04', 'Enc_Nbr': 8307587}],
 65557: [{'Enc_Date': '2015-04-15', 'Enc_Nbr': 776480},
  {'Enc_Date': '2016-04-

In [21]:
set(Enc_list.keys())&set(demographics.keys())==set(Enc_list)
# People in demographics have fully covered people in encouters

True

In [58]:
set(Enc_list)&set(family_hist_list) == set(family_hist_list)
# People has family history record must have encounter records, encounters fully cover family_hist_list

True

### Merge into a dictionary of profile

In [72]:
profile_full={}
for k,v in demographics.items():
    profile_full[k]=v
    
    # patint may or may nor have a family history
    profile_full[k]['family_hist_list'] = {}
    profile_full[k]['family_hist_list_count'] = 0
    if k in family_hist_list.keys():
        profile_full[k]['family_hist_list'] = family_hist_list[k]
        profile_full[k]['family_hist_list_count'] = len(family_hist_list[k])
    
    # patient may or may not have encounter records
    profile_full[k]['Enc_list'] = {}
    profile_full[k]['Enc_list_count'] = 0
    if k in Enc_list.keys():
        profile_full[k]['Enc_list'] = Enc_list[k]
        profile_full[k]['Enc_list_count'] = len(Enc_list[k])

In [73]:
profile_full

{174763: {'Age': 45,
  'Age_Censored': 'None',
  'Enc_list': [{'Enc_Date': '2013-01-28', 'Enc_Nbr': 2668725},
   {'Enc_Date': '2014-12-07', 'Enc_Nbr': 2508769},
   {'Enc_Date': '2015-01-13', 'Enc_Nbr': 6641400}],
  'Enc_list_count': 3,
  'Ethnicity': 'Hispanic or Latino',
  'Gender': 'F',
  'Race': 'Hispanic',
  'family_hist_list': {'Father': [{'Code': 'NULL', 'Family_history': 'HBP'},
    {'Code': '160302006', 'Family_history': 'Thyroid disorder'}],
   'Mother': [{'Code': '416855002', 'Family_history': 'Diabetes mellitus'},
    {'Code': 'NULL', 'Family_history': 'HBP'}]},
  'family_hist_list_count': 2,
  'zip_code': '60609'},
 622597: {'Age': 55,
  'Age_Censored': 'None',
  'Enc_list': [{'Enc_Date': '2013-05-02', 'Enc_Nbr': 16488561},
   {'Enc_Date': '2013-05-02', 'Enc_Nbr': 13216606},
   {'Enc_Date': '2014-12-19', 'Enc_Nbr': 6333408},
   {'Enc_Date': '2014-12-19', 'Enc_Nbr': 9923528}],
  'Enc_list_count': 4,
  'Ethnicity': 'Declined to specify',
  'Gender': 'F',
  'Race': 'Declined t

In [74]:
len(profile_full)

17019

Shall we remove the profiles that has no history and no encounters? 

In [64]:
len(set(demographics)-set(family_hist_list))
# That is to remove 2975 patients

2975

In [25]:
len(set(family_hist_list)&set(Enc_list))
# So that only 14044 patients left have both records

14044

In [65]:
len(set(demographics)-set(Enc_list))

510

We have in total 17019 patients. 510 of total have no encounter records. 2465 of total have no encounter records and no family records. If we want a profile that everyone has both records, we need to remove all 2975 patients. 

In [31]:
# Remove patients have no family or no encounter records
profile={}
for k,v in demographics.items():
    if k in set(family_hist_list)&set(Enc_list):
        profile[k]=v
        
        profile[k]['family_hist_list'] = family_hist_list[k]
        profile[k]['family_hist_list_count'] = len(family_hist_list[k])

        profile[k]['Enc_list'] = Enc_list[k]
        profile[k]['Enc_list_count'] = len(Enc_list[k])
    else:
        continue

In [32]:
profile

{109227: {'Age': 61,
  'Age_Censored': 'None',
  'Enc_list': [{'Enc_Date': '2016-07-29', 'Enc_Nbr': 4086734}],
  'Enc_list_count': 1,
  'Ethnicity': 'Not Hispanic or Latino',
  'Gender': 'F',
  'Race': 'Black/African American (Not Hispanic)',
  'family_hist_list': {'Brother': [{'Code': '430679000',
     'Family_history': 'Diabetes mellitus type 2'}],
   'Father': [{'Code': '160274005',
     'Family_history': 'No history of Diabetes mellitus'},
    {'Code': '160267000', 'Family_history': 'No history of Glaucoma'}],
   'Mother': [{'Code': '416855002', 'Family_history': 'Diabetes mellitus'},
    {'Code': '160267000', 'Family_history': 'No history of Glaucoma'},
    {'Code': '160357008', 'Family_history': 'Hypertension'}]},
  'family_hist_list_count': 3,
  'zip_code': '60419'},
 622597: {'Age': 55,
  'Age_Censored': 'None',
  'Enc_list': [{'Enc_Date': '2013-05-02', 'Enc_Nbr': 16488561},
   {'Enc_Date': '2013-05-02', 'Enc_Nbr': 13216606},
   {'Enc_Date': '2014-12-19', 'Enc_Nbr': 6333408},
 

In [70]:
len(profile)

14044

(Or we can only remove 510 patients that lack encounter records and omit family part for now)

In [66]:
# Remove patients have no encounter records
profile1={}
for k,v in demographics.items():
    if k in set(Enc_list):
        profile1[k]=v

        profile1[k]['Enc_list'] = Enc_list[k]
        profile1[k]['Enc_list_count'] = len(Enc_list[k])
        
        profile1[k]['family_hist_list'] = {}
        profile1[k]['family_hist_list_count'] = 0
        
        if k in family_hist_list.keys():
            profile1[k]['family_hist_list'] = family_hist_list[k]
            profile1[k]['family_hist_list_count'] = len(family_hist_list[k])
    else:
        continue

In [67]:
profile1

{174763: {'Age': 45,
  'Age_Censored': 'None',
  'Enc_list': [{'Enc_Date': '2013-01-28', 'Enc_Nbr': 2668725},
   {'Enc_Date': '2014-12-07', 'Enc_Nbr': 2508769},
   {'Enc_Date': '2015-01-13', 'Enc_Nbr': 6641400}],
  'Enc_list_count': 3,
  'Ethnicity': 'Hispanic or Latino',
  'Gender': 'F',
  'Race': 'Hispanic',
  'family_hist_list': {'Father': [{'Code': 'NULL', 'Family_history': 'HBP'},
    {'Code': '160302006', 'Family_history': 'Thyroid disorder'}],
   'Mother': [{'Code': '416855002', 'Family_history': 'Diabetes mellitus'},
    {'Code': 'NULL', 'Family_history': 'HBP'}]},
  'family_hist_list_count': 2,
  'zip_code': '60609'},
 622597: {'Age': 55,
  'Age_Censored': 'None',
  'Enc_list': [{'Enc_Date': '2013-05-02', 'Enc_Nbr': 16488561},
   {'Enc_Date': '2013-05-02', 'Enc_Nbr': 13216606},
   {'Enc_Date': '2014-12-19', 'Enc_Nbr': 6333408},
   {'Enc_Date': '2014-12-19', 'Enc_Nbr': 9923528}],
  'Enc_list_count': 4,
  'Ethnicity': 'Declined to specify',
  'Gender': 'F',
  'Race': 'Declined t

In [69]:
len(profile1)

16509

### Tried to export  profile as json file
We need an intermediate data that is processed, otherwise it may be too slow

In [75]:
import json
json1=json.dumps(profile, ensure_ascii=False)

In [76]:
with open('person_profile.json', 'w') as fp:
    json.dump(profile, fp)

In [78]:
json2=json.loads(json1)

In [79]:
type(json1)

str

In [80]:
type(json2)

dict

In [82]:
json2['33']

{u'Age': 69,
 u'Age_Censored': u'None',
 u'Enc_list': [{u'Enc_Date': u'2014-12-18', u'Enc_Nbr': 123227}],
 u'Enc_list_count': 1,
 u'Ethnicity': u'Declined to specify',
 u'Gender': u'F',
 u'Race': u'Black/African American (Not Hispanic)',
 u'family_hist_list': {u'Brother': [{u'Code': u'439724007',
    u'Family_history': u'Heart disease'}],
  u'Father': [{u'Code': u'160347007', u'Family_history': u'Glaucoma'},
   {u'Code': u'160274005',
    u'Family_history': u'No history of Diabetes mellitus'}],
  u'Mother': [{u'Code': u'160274005',
    u'Family_history': u'No history of Diabetes mellitus'},
   {u'Code': u'160267000', u'Family_history': u'No history of Glaucoma'}],
  u'Sister': [{u'Code': u'439724007', u'Family_history': u'Heart disease'}]},
 u'family_hist_list_count': 4,
 u'zip_code': u'60616'}

In [28]:
# json file is able to export. But there seems a problem with reading back in
pd.read_json('person_profile.json', orient='values')

ValueError: Expected object or value

### Tried to export profile as csv file

In [83]:
import csv
with open('person_profile.csv', 'wb') as csv_file:
    writer = csv.writer(csv_file)
    for key, value in profile.items():
       writer.writerow([key, value])

In [89]:
pd.read_csv('person_profile.csv', names=['Person_Nbr', 'f'])

Person_Nbr                                                  f
0          109227  {'Gender': 'F', 'Age': 61, 'Enc_list': [{'Enc_...
1          622597  {'Gender': 'F', 'Age': 55, 'Enc_list': [{'Enc_...
2          196620  {'Gender': 'M', 'Age': 52, 'Enc_list': [{'Enc_...
3          884751  {'Gender': 'M', 'Age': 60, 'Enc_list': [{'Enc_...
4          819216  {'Gender': 'F', 'Age': 24, 'Enc_list': [{'Enc_...
5           98322  {'Gender': 'M', 'Age': 60, 'Enc_list': [{'Enc_...
6         1015827  {'Gender': 'F', 'Age': 64, 'Enc_list': [{'Enc_...
7           65557  {'Gender': 'F', 'Age': 55, 'Enc_list': [{'Enc_...
8          360473  {'Gender': 'F', 'Age': 41, 'Enc_list': [{'Enc_...
9          614307  {'Gender': 'M', 'Age': 86, 'Enc_list': [{'Enc_...
10             33  {'Gender': 'F', 'Age': 69, 'Enc_list': [{'Enc_...
11         524323  {'Gender': 'F', 'Age': 55, 'Enc_list': [{'Enc_...
12          65572  {'Gender': 'M', 'Age': 73, 'Enc_list': [{'Enc_...
13         917541  {'Gender': 'M', 'Age': 49, 'Enc_list': [{'Enc_...
14         688167  {'Gender': 'F', 'Age': 78, 'Enc_list': [{'Enc_...
15         786478  {'Gender': 'M', 'Age': 76, 'Enc_list': [{'Enc_...
16         524336  {'Gender': 'M', 'Age': 57, 'Enc_list': [{'Enc_...
17         491573  {'Gender': 'M', 'Age': 57, 'Enc_list': [{'Enc_...
18         983094  {'Gender': 'M', 'Age': 82, 'Enc_list': [{'Enc_...
19         327736  {'Gender': 'F', 'Age': 54, 'Enc_list': [{'Enc_...
20         524352  {'Gender': 'F', 'Age': 60, 'Enc_list': [{'Enc_...
21         655425  {'Gender': 'M', 'Age': 69, 'Enc_list': [{'Enc_...
22         852036  {'Gender': 'F', 'Age': 71, 'Enc_list': [{'Enc_...
23         458764  {'Gender': 'M', 'Age': 37, 'Enc_list': [{'Enc_...
24         327754  {'Gender': 'F', 'Age': 55, 'Enc_list': [{'Enc_...
25         196684  {'Gender': 'F', 'Age': 69, 'Enc_list': [{'Enc_...
26         884813  {'Gender': 'F', 'Age': 31, 'Enc_list': [{'Enc_...
27         890211  {'Gender': 'F', 'Age': 51, 'Enc_list': [{'Enc_...
28             89  {'Gender': 'M', 'Age': 62, 'Enc_list': [{'Enc_...
29         262235  {'Gender': 'F', 'Age': 59, 'Enc_list': [{'Enc_...
...           ...                                                ...
14014      622530  {'Gender': 'M', 'Age': 87, 'Enc_list': [{'Enc_...
14015      622532  {'Gender': 'F', 'Age': 54, 'Enc_list': [{'Enc_...
14016      425930  {'Gender': 'F', 'Age': 79, 'Enc_list': [{'Enc_...
14017      655351  {'Gender': 'M', 'Age': 56, 'Enc_list': [{'Enc_...
14018      294860  {'Gender': 'M', 'Age': 55, 'Enc_list': [{'Enc_...
14019      993954  {'Gender': 'F', 'Age': 60, 'Enc_list': [{'Enc_...
14020      327631  {'Gender': 'M', 'Age': 52, 'Enc_list': [{'Enc_...
14021     1048528  {'Gender': 'M', 'Age': 42, 'Enc_list': [{'Enc_...
14022      131027  {'Gender': 'F', 'Age': 64, 'Enc_list': [{'Enc_...
14023      873806  {'Gender': 'M', 'Age': 66, 'Enc_list': [{'Enc_...
14024      983000  {'Gender': 'M', 'Age': 61, 'Enc_list': [{'Enc_...
14025      393179  {'Gender': 'F', 'Age': 68, 'Enc_list': [{'Enc_...
14026      393180  {'Gender': 'F', 'Age': 70, 'Enc_list': [{'Enc_...
14027      917470  {'Gender': 'M', 'Age': 67, 'Enc_list': [{'Enc_...
14028      557023  {'Gender': 'F', 'Age': 36, 'Enc_list': [{'Enc_...
14029      425953  {'Gender': 'M', 'Age': 55, 'Enc_list': [{'Enc_...
14030      753634  {'Gender': 'M', 'Age': 59, 'Enc_list': [{'Enc_...
14031      753636  {'Gender': 'F', 'Age': 66, 'Enc_list': [{'Enc_...
14032      131045  {'Gender': 'M', 'Age': 42, 'Enc_list': [{'Enc_...
14033      262118  {'Gender': 'M', 'Age': 68, 'Enc_list': [{'Enc_...
14034     1037649  {'Gender': 'F', 'Age': 60, 'Enc_list': [{'Enc_...
14035      753641  {'Gender': 'F', 'Age': 80, 'Enc_list': [{'Enc_...
14036      491498  {'Gender': 'F', 'Age': 89, 'Enc_list': [{'Enc_...
14037      929200  {'Gender': 'M', 'Age': 56, 'Enc_list': [{'Enc_...
14038      157122  {'Gender': 'M', 'Age': 66, 'Enc_list': [{'Enc_...
14039      425970  {'Gender': 'F', 'Age': 57, 'Enc_list': [{'Enc_...
14040

### Read profile into pandas dataframe

In [33]:
# If we read dict back into data frame, Person_Nbr will be index 
temp=DataFrame.from_dict(profile, orient='index')
temp.head()

Gender  Age                                           Enc_list  \
33       F   69  [{u'Enc_Date': u'2014-12-18', u'Enc_Nbr': 1232...   
89       M   62  [{u'Enc_Date': u'2012-10-16', u'Enc_Nbr': 1287...   
146      F   69  [{u'Enc_Date': u'2012-11-04', u'Enc_Nbr': 9086...   
196      F   62  [{u'Enc_Date': u'2016-10-05', u'Enc_Nbr': 1453...   
331      M   59  [{u'Enc_Date': u'2015-12-01', u'Enc_Nbr': 2071...   

    Age_Censored                                   family_hist_list  \
33          None  {u'Sister': [{u'Code': u'439724007', u'Family_...   
89          None  {u'Paternal uncle': [{u'Code': u'160347007', u...   
146         None  {u'Father': [{u'Code': u'416855002', u'Family_...   
196         None  {u'Father': [{u'Code': u'160274005', u'Family_...   
331         None  {u'Father': [{u'Code': u'160274005', u'Family_...   

     Enc_list_count                                   Race  \
33                1  Black/African American (Not Hispanic)   
89                9                    Declined to specify   
146               5                    Declined to specify   
196               2                    Declined to specify   
331               3  Black/African American (Not Hispanic)   

     family_hist_list_count               Ethnicity zip_code  
33                        4     Declined to specify    60616  
89                        3     Declined to specify    60652  
146                       2     Declined to specify    60615  
196                       2     Declined to specify    60615  
331                       3  Not Hispanic or Latino    60620

In [34]:
# encounter list can be accessed with dataframe
temp.loc[89, 'Enc_list']

[{'Enc_Date': '2012-10-16', 'Enc_Nbr': 12870648},
 {'Enc_Date': '2014-03-12', 'Enc_Nbr': 4126172},
 {'Enc_Date': '2014-04-17', 'Enc_Nbr': 9217142},
 {'Enc_Date': '2014-05-25', 'Enc_Nbr': 14968450},
 {'Enc_Date': '2015-03-14', 'Enc_Nbr': 14537805},
 {'Enc_Date': '2015-07-11', 'Enc_Nbr': 13815981},
 {'Enc_Date': '2015-07-14', 'Enc_Nbr': 455661},
 {'Enc_Date': '2016-10-22', 'Enc_Nbr': 10658304},
 {'Enc_Date': '2016-10-22', 'Enc_Nbr': 233159}]

In [39]:
# Family history can also be accessed
temp.loc[89, 'family_hist_list']

{'Father': [{'Code': '160274005',
   'Family_history': 'No history of Diabetes mellitus'},
  {'Code': '160267000', 'Family_history': 'No history of Glaucoma'}],
 'Mother': [{'Code': '416855002', 'Family_history': 'Diabetes mellitus'},
  {'Code': '160267000', 'Family_history': 'No history of Glaucoma'}],
 'Paternal uncle': [{'Code': '160347007', 'Family_history': 'Glaucoma'}]}

In [92]:
temp.to_csv('person_profile.csv')

### Tried to process snomed code list

In [35]:
dfs[3].head()

Person_ID  Person_Nbr  \
51792  80d3df88-dddf-5ad3-7cc1-b7b1ac6151fa          33   
51793  80d3df88-dddf-5ad3-7cc1-b7b1ac6151fa          33   
51791  80d3df88-dddf-5ad3-7cc1-b7b1ac6151fa          33   
32043  adca6fa4-e7d4-d7f8-cf41-27056662d84b          89   
24288  ca793eec-f101-2505-42e6-57fefc6baf14         146   

                 Date_Created Snomed_Code      Systemic_Diseases  
51792 2014-12-18 14:34:34.807    44054006        Diabetes type 2  
51793 2014-12-18 14:34:39.193    38341003           Hypertension  
51791 2014-12-18 14:34:52.520        NULL       High cholesterol  
32043 2015-07-14 11:36:54.970        NULL  Narrow angle glaucoma  
24288 2012-11-04 19:07:22.160    55822004           Hypertension

In [36]:
dfs[4].head()

Person_ID  Person_Nbr  \
69610  80d3df88-dddf-5ad3-7cc1-b7b1ac6151fa          33   
69608  80d3df88-dddf-5ad3-7cc1-b7b1ac6151fa          33   
69609  80d3df88-dddf-5ad3-7cc1-b7b1ac6151fa          33   
46510  adca6fa4-e7d4-d7f8-cf41-27056662d84b          89   
46511  adca6fa4-e7d4-d7f8-cf41-27056662d84b          89   

                 Date_Created  Concept_ID  \
69610 2014-12-18 15:51:19.607    41256004   
69608 2014-12-18 15:51:28.043    41446000   
69609 2014-12-18 16:36:28.083   313436004   
46510 2014-08-12 03:04:55.010    81416004   
46511 2014-08-12 03:04:55.010    28998008   

                                         Description  
69610                                     Presbyopia  
69608                                    Blepharitis  
69609  Type 2 diabetes mellitus without complication  
46510            Open angle with borderline findings  
46511                             Retinal hemorrhage

In [37]:
{k:list(v) for k,v in dfs[3].groupby('Person_Nbr')['Snomed_Code']}

{109227: ['44054006', '56265001', '38341003', '230690007', '13644009'],
 622597: ['73211009',
  '55822004',
  '40930008',
  '363358000',
  'NULL',
  '73430006',
  'NULL'],
 196620: ['NULL',
  '195967001',
  'NULL',
  'NULL',
  '195967001',
  '35489007',
  'NULL',
  '3723001'],
 884751: ['4855003',
  '4855003',
  '55822004',
  'NULL',
  'NULL',
  '13644009',
  '4855003',
  '4855003'],
 819216: ['NULL', 'NULL'],
 98322: ['NULL', '38341003', '14304000'],
 1015827: ['73211009', '38341003', '14304000', 'NULL', 'NULL'],
 65557: ['195967001',
  '44054006',
  '13644009',
  '38341003',
  '197480006',
  '3723001',
  '14304000',
  'NULL',
  'NULL'],
 360473: ['44054006', '35489007'],
 33: ['44054006', '38341003', 'NULL'],
 524323: ['38341003', '44054006'],
 65572: ['55822004', 'NULL', '230690007', 'NULL', 'NULL', 'NULL'],
 917541: ['NULL'],
 393254: ['NULL', '3723001'],
 688167: ['4855003'],
 106932: ['NULL', 'NULL', 'NULL', 'NULL'],
 98348: ['NULL', '55822004'],
 786478: ['44054006',
  '38341003

In [38]:
{k:list(v) for k,v in dfs[4].groupby('Person_Nbr')['Concept_ID']}

{109227: [38101003, 111552007, 41446000],
 622597: [46152009, 41256004, 313436004, 42513006],
 196620: [41256004, 57190000, 46152009, 82649003],
 884751: [59276001, 57190000, 41256004, 82649003],
 819216: [68478007],
 98322: [82649003, 46152009, 111552007, 38101003],
 1015827: [41256004, 399054005, 35600002, 6962006, 46152009],
 65557: [247133006, 57190000, 6962006, 111552007],
 360473: [38101003, 46152009, 73211009],
 33: [41256004, 41446000, 313436004],
 524323: [44054006, 59621000, 41256004],
 65572: [38101003,
  68905002,
  41256004,
  81416004,
  57190000,
  41446000,
  11422002,
  84494001,
  77075001,
  76976005,
  14357004],
 917541: [81416004, 41256004, 57190000, 82649003],
 393254: [38101003, 77075001, 76976005, 86643000],
 688167: [312905005,
  41256004,
  77075001,
  312903003,
  11422002,
  81416004,
  21011008],
 106932: [47337003, 57190000, 161676006],
 98348: [46152009, 82649003, 46622000, 41256004],
 786478: [41256004,
  193570009,
  422034002,
  161483005,
  161483005